## Oliwier Misztal   --------------   December 2, 2025
## Arthur Murphy
## Javi Jorge
# Molecular Modeling - Monte Carlo Methods

In [25]:
import numpy as np
# constants
L = 10            # lattice size
N = L**2          # total sites (100 spins)
T = 2.0           # Temperature
MCS = 10000       # number of steps to take
meas = 25         # measurement frequency


In [26]:
def create_nbr(L):
  nbr = np.zeros(shape=(L**2, 4), dtype=int)
  ip = np.arange(L) + 1
  im = np.arange(L) - 1
  ip[L - 1] = 0
  im[0] = L - 1
  for x in range(L):
    for y in range(L):
      i = x + y * L
      nbr[i, 0] = ip[x] + y * L  #right neighbor
      nbr[i, 1] = im[x] + y * L  #left neighbor
      nbr[i, 2] = x + ip[y] * L  #above neighbor
      nbr[i, 3] = x + im[y] * L  #below neighbor
  return nbr

In [27]:
nbr = create_nbr(L)
nbr

array([[ 1,  9, 10, 90],
       [ 2,  0, 11, 91],
       [ 3,  1, 12, 92],
       [ 4,  2, 13, 93],
       [ 5,  3, 14, 94],
       [ 6,  4, 15, 95],
       [ 7,  5, 16, 96],
       [ 8,  6, 17, 97],
       [ 9,  7, 18, 98],
       [ 0,  8, 19, 99],
       [11, 19, 20,  0],
       [12, 10, 21,  1],
       [13, 11, 22,  2],
       [14, 12, 23,  3],
       [15, 13, 24,  4],
       [16, 14, 25,  5],
       [17, 15, 26,  6],
       [18, 16, 27,  7],
       [19, 17, 28,  8],
       [10, 18, 29,  9],
       [21, 29, 30, 10],
       [22, 20, 31, 11],
       [23, 21, 32, 12],
       [24, 22, 33, 13],
       [25, 23, 34, 14],
       [26, 24, 35, 15],
       [27, 25, 36, 16],
       [28, 26, 37, 17],
       [29, 27, 38, 18],
       [20, 28, 39, 19],
       [31, 39, 40, 20],
       [32, 30, 41, 21],
       [33, 31, 42, 22],
       [34, 32, 43, 23],
       [35, 33, 44, 24],
       [36, 34, 45, 25],
       [37, 35, 46, 26],
       [38, 36, 47, 27],
       [39, 37, 48, 28],
       [30, 38, 49, 29],


In [28]:
# magnetization calculation
def calc_magnetization(state):
    return np.sum(state) / N

In [29]:
spins = np.ones(shape=N, dtype=int)
spins

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1])

In [30]:
#numpy array with 100 elements randomly set to +1 or -1
spins = np.random.choice([-1, 1], size=N)
spins

array([-1,  1,  1,  1, -1,  1,  1, -1,  1,  1, -1,  1,  1,  1,  1,  1,  1,
       -1, -1,  1, -1, -1,  1, -1, -1, -1,  1, -1,  1,  1,  1, -1, -1, -1,
        1, -1,  1,  1, -1, -1, -1,  1, -1, -1, -1, -1,  1,  1,  1, -1, -1,
        1, -1, -1, -1,  1,  1, -1,  1,  1, -1, -1, -1, -1,  1, -1,  1,  1,
        1, -1,  1,  1, -1,  1, -1,  1,  1,  1, -1, -1,  1,  1, -1,  1,  1,
        1, -1,  1,  1,  1,  1,  1, -1, -1, -1, -1, -1, -1, -1, -1])

In [31]:
#import test_configuration file as test_config
test_config = np.loadtxt('test_configuration.dat', dtype=int)
test_spins = test_config[:,1]

In [32]:
#energy calculation for test configuration L=10
def calc_energy(state, nbr):
    energy = 0
    #magnetization = 0
    for i in range(N):
        i_state = state[i]
        current_energy = 0
        for j in range(4):
            current_energy -= state[nbr[i, j]]
        energy += i_state * current_energy
        #magnetization += i_state
    #return energy/2, magnetization  # each pair counted twice
    return energy/2  # each pair counted twice
#test_config_energy, test_config_magnetization = calc_energy(test_spins, nbr)
test_config_energy = calc_energy(test_spins, nbr)
print("Test configuration energy:", test_config_energy)
#print("Test configuration magnetization:", test_config_magnetization)
print("Test configuration magnetization:", np.sum(test_spins))

Test configuration energy: -8.0
Test configuration magnetization: 8


In [47]:
#choose a random spin to flip
# def propose_flip(state):
#     proposed_state = state.copy()
#     flip_index = np.random.randint(0, N)
#     proposed_state[flip_index] *= -1
#     return proposed_state

def step_once(current_state, nbr, beta=1/T):
    print("Current state before flip:", current_state)
    flip_index = np.random.randint(0, N)
    #use nbr array to determine sum of their energies
    nbrs = nbr[flip_index]
    print("Neighbors indices:", nbrs)
    nbr_sum = np.sum(current_state[nbrs])
    delta_E = 2 * current_state[flip_index] * nbr_sum
    print("Flipping index:", flip_index)
    print("Neighbor sum:", nbr_sum)
    print("Delta E:", delta_E)
    if (delta_E < 0) or (np.random.rand() < np.exp(-beta * delta_E)):
        current_state[flip_index] *= -1
    return current_state


# test 100 step_once and print energy each time


In [49]:
for step in range(100):
    for switch_step in range(N):
        test_spins = step_once(test_spins, nbr)
    if (step + 1) % 10 == 0:
        energy = calc_energy(test_spins, nbr)
        print(f"Step {step+1}, Energy: {energy}")

Current state before flip: [-1 -1  1  1  1 -1  1 -1 -1 -1  1 -1 -1  1  1  1 -1 -1 -1  1  1 -1 -1 -1
  1 -1  1 -1  1 -1  1  1  1  1  1 -1  1  1  1 -1  1 -1  1 -1  1  1  1 -1
 -1 -1 -1  1  1  1 -1  1  1  1  1  1 -1  1  1  1 -1  1 -1 -1  1 -1 -1  1
  1  1 -1 -1 -1 -1  1  1  1 -1 -1 -1  1 -1 -1  1  1  1  1 -1 -1 -1  1  1
  1 -1  1 -1]
Neighbors indices: [35 33 44 24]
Flipping index: 34
Neighbor sum: 2
Delta E: 4
Current state before flip: [-1 -1  1  1  1 -1  1 -1 -1 -1  1 -1 -1  1  1  1 -1 -1 -1  1  1 -1 -1 -1
  1 -1  1 -1  1 -1  1  1  1  1 -1 -1  1  1  1 -1  1 -1  1 -1  1  1  1 -1
 -1 -1 -1  1  1  1 -1  1  1  1  1  1 -1  1  1  1 -1  1 -1 -1  1 -1 -1  1
  1  1 -1 -1 -1 -1  1  1  1 -1 -1 -1  1 -1 -1  1  1  1  1 -1 -1 -1  1  1
  1 -1  1 -1]
Neighbors indices: [63 61 72 52]
Flipping index: 62
Neighbor sum: 4
Delta E: 8
Current state before flip: [-1 -1  1  1  1 -1  1 -1 -1 -1  1 -1 -1  1  1  1 -1 -1 -1  1  1 -1 -1 -1
  1 -1  1 -1  1 -1  1  1  1  1 -1 -1  1  1  1 -1  1 -1  1 -1  1  1  1 -1
 -1